In [ ]:
import tensorflow as tf
import pandas as pd

from tensorforce.agents import Agent

from tensortrade.strategies import TensorforceTradingStrategy
from tensortrade.environments import TradingEnvironment
from tensortrade.rewards import RiskAdjustedReturns
from tensortrade.actions import PairCriteriaSizeActions
from tensortrade.instruments import Quantity, TradingPair, BTC, USD
from tensortrade.orders.criteria import StopLossCriteria, StopDirection
from tensortrade.wallets import Wallet, Portfolio
from tensortrade.exchanges.simulated import SimulatedExchange
from tensortrade.features.stationarity import FractionalDifference
from tensortrade.features.scalers import MinMaxNormalizer
from tensortrade.features import FeaturePipeline

WINDOW_SIZE = 1
PRICE_COLUMN = 'close'

normalize = MinMaxNormalizer(inplace=True)
difference = FractionalDifference(difference_order=0.6, inplace=True)
feature_pipeline = FeaturePipeline(steps=[normalize, difference])

criteria = [None, StopLossCriteria(StopDirection.UP), StopLossCriteria(StopDirection.DOWN)]

action_scheme = PairCriteriaSizeActions(USD/BTC, criteria=criteria)
reward_scheme = RiskAdjustedReturns(return_algorithm="sortino")

csv_file = tf.keras.utils.get_file(
    'Coinbase_BTCUSD_1h.csv', 'https://www.cryptodatadownload.com/cdd/Coinbase_BTCUSD_1h.csv')
ohlcv_data = pd.read_csv(csv_file, skiprows=1, index_col="Date")
ohlcv_data.columns = map(str.lower, ohlcv_data.columns)
ohlcv_data = ohlcv_data.rename(columns={'volume btc': 'volume'})

# ohlcv_data = pd.read_csv('./data/updateOHLCdata_master.csv')
ohlcv_data = ohlcv_data.iloc[0:10000]

exchange = SimulatedExchange(data_frame=ohlcv_data, price_column=PRICE_COLUMN)

wallets = [(exchange, USD, 10000), (exchange, BTC, 0)]

portfolio = Portfolio(base_instrument=USD, wallet_tuples=wallets)

print('Transformed Data:')
print(exchange.observation_columns)


environment = TradingEnvironment(exchange=exchange,
                                 portfolio=portfolio,
                                 action_scheme=action_scheme,
                                 reward_scheme=reward_scheme,
                                 feature_pipeline=feature_pipeline,
                                 window_size=WINDOW_SIZE)

strategy = TensorforceTradingStrategy(environment=environment,
                                      agent='ppo',
                                      max_episode_timesteps=10000)

performance = strategy.run(steps=10000)

W1209 00:12:02.615777 4539641280 deprecation_wrapper.py:119] From /usr/local/lib/python3.7/site-packages/tensorforce/core/module.py:31: The name tf.enable_resource_variables is deprecated. Please use tf.compat.v1.enable_resource_variables instead.

W1209 00:12:02.632996 4539641280 deprecation_wrapper.py:119] From /usr/local/lib/python3.7/site-packages/tensorforce/core/optimizers/tf_optimizer.py:46: The name tf.train.AdadeltaOptimizer is deprecated. Please use tf.compat.v1.train.AdadeltaOptimizer instead.

W1209 00:12:02.633752 4539641280 deprecation_wrapper.py:119] From /usr/local/lib/python3.7/site-packages/tensorforce/core/optimizers/tf_optimizer.py:47: The name tf.train.AdagradOptimizer is deprecated. Please use tf.compat.v1.train.AdagradOptimizer instead.

W1209 00:12:02.634443 4539641280 deprecation_wrapper.py:119] From /usr/local/lib/python3.7/site-packages/tensorforce/core/optimizers/tf_optimizer.py:48: The name tf.train.AdamOptimizer is deprecated. Please use tf.compat.v1.train

Transformed Data:
Index(['open', 'high', 'low', 'close', 'volume', 'volume usd'], dtype='object')
Current price: 11590.0


Timesteps:   0%|          | 0/10000 [00:00<?, ?it/s, mean_reward=n/a]

Current price: 11590.0
Action: TradeSide.BUY | USD/BTC | 0.5 | Take Profit: 0.02
Balance Wallet: Balance: 10000.00 USD | Locked: 0.00 USD
Order:  OrderStatus.PENDING | TradeSide.BUY | TradeType.MARKET | USD/BTC | 5000.00 USD | 11622.61 | Take Profit: 0.02
Current price: 11622.61
Portfolio:     BTC  BTC_locked     USD  USD_locked  net_worth step
0  0.0         0.0  5000.0      5000.0    10000.0    0
Reward:  0.0
Current price: 11518.22
Profit loss:  1.0
Current price: 11518.22
Action: TradeSide.SELL | USD/BTC | 0.1 | None
Balance Wallet: Balance: 0.00000000 BTC | Locked: 0.00000000 BTC
Order:  None
Current price: 11518.22
Portfolio:     BTC  BTC_locked     USD  USD_locked  net_worth step
0  0.0         0.0  5000.0      5000.0    10000.0    0
0  0.0         0.0  5000.0      5000.0    10000.0    1
Reward:  0.0
Current price: 11463.01
Profit loss:  1.0
Current price: 11463.01
Action: TradeSide.BUY | USD/BTC | 0.25 | Take Profit: 0.02
Balance Wallet: Balance: 5000.00 USD | Locked: 5000.00 U

Reward:  0.12100776717810462
Current price: 11668.0
Profit loss:  0.9980446684639999
Current price: 11668.0
Action: TradeSide.BUY | USD/BTC | 0.14285714285714285 | Stop Loss: 0.02
Balance Wallet: Balance: 834.12 USD | Locked: 5009.28 USD
Order:  OrderStatus.PENDING | TradeSide.BUY | TradeType.MARKET | USD/BTC | 119.16 USD | 11668.0 | Stop Loss: 0.02
Current price: 11668.0
Portfolio:          BTC  BTC_locked     USD  USD_locked     net_worth step
0  0.425476         0.0    5.50     5003.78  10019.249137   10
0  0.425476         0.0    0.00     5009.28   9987.678806   11
0  0.425476         0.0    0.00     5009.28   9999.745310   12
0  0.354563         0.0  834.12     5009.28  10026.532846   13
0  0.354563         0.0  714.96     5128.44   9980.446685   14
Reward:  -0.056923504223956055
Current price: 11767.54
Profit loss:  1.0015739933439198
Current price: 11767.54
Action: TradeSide.SELL | USD/BTC | 0.2 | Take Profit: 0.02
Balance Wallet: Balance: 0.35456348 BTC | Locked: 0.00000000 BTC

...

Before: Balance: 1.34 USD | Locked: 4970.96 USD | Balance: 0.00151361 BTC | Locked: 0.40843554 BTC
After: Balance: 1.34 USD | Locked: 4972.25 USD | Balance: 0.00151361 BTC | Locked: 0.40828210 BTC
Current price: 8435.0
Portfolio:          BTC  BTC_locked   USD  USD_locked    net_worth  step
0  0.000192    0.408531  0.00     4982.65  8350.075023  9065
0  0.000228    0.408553  0.00     4982.17  8370.966148  9066
0  0.000210    0.408568  0.26     4981.94  8389.191606  9067
0  0.000210    0.408568  0.22     4981.99  8390.153476  9068
0  0.001514    0.408282  2.63     4970.96  8430.216814  9069
Reward:  -0.0036077863160701284
Current price: 8416.19
Profit loss:  0.8422508556544901
Current price: 8416.19
Action: TradeSide.BUY | USD/BTC | 0.1111111111111111 | Stop Loss: 0.02
Balance Wallet: Balance: 2.63 USD | Locked: 4970.96 USD
Order:  OrderStatus.PENDING | TradeSide.BUY | TradeType.MARKET | USD/BTC | 0.29 USD | 8416.19 | Stop Loss: 0.02
Current price: 8416.19
Portfolio:          BTC  BTC_l

Action: TradeSide.BUY | USD/BTC | 1.0 | Stop Loss: 0.02
Balance Wallet: Balance: 2.09 USD | Locked: 4973.10 USD
Order:  OrderStatus.PENDING | TradeSide.BUY | TradeType.MARKET | USD/BTC | 2.09 USD | 8176.94 | Stop Loss: 0.02
Current price: 8176.94
Portfolio:          BTC  BTC_locked   USD  USD_locked    net_worth  step
0  0.000765    0.408739  3.93     4972.05  8345.776915  9078
0  0.000637    0.408866  3.93     4972.05  8356.239719  9079
0  0.000732    0.408866  3.14     4972.05  8352.737829  9080
0  0.000732    0.408866  2.09     4973.10  8345.528899  9081
0  0.000732    0.408866  0.00     4975.19  8324.450969  9082
Reward:  -0.0038466981942134955
Current price: 8181.7
Profit loss:  0.8326400656560999
Current price: 8181.7
Action: TradeSide.BUY | USD/BTC | 0.125 | Stop Loss: 0.02
Balance Wallet: Balance: 0.00 USD | Locked: 4975.19 USD
Order:  None
Current price: 8181.7
Portfolio:          BTC  BTC_locked   USD  USD_locked    net_worth  step
0  0.000637    0.408866  3.93     4972.05  8

Portfolio:          BTC  BTC_locked   USD  USD_locked    net_worth  step
0  0.001066    0.408957  0.50     4971.29  8257.304633  9089
0  0.000533    0.409482  0.56     4971.29  8247.053681  9090
0  0.000556    0.409482  0.37     4971.29  8254.838750  9091
0  0.000556    0.409478  0.35     4971.34  8243.765071  9092
0  0.000464    0.409478  1.09     4971.34  8242.756469  9093
Reward:  -0.004030398593795276
Current price: 7849.99
Profit loss:  0.81904684025828
Current price: 7849.99
Action: TradeSide.BUY | USD/BTC | 1.0 | None
Balance Wallet: Balance: 1.09 USD | Locked: 4971.34 USD
Order:  OrderStatus.PENDING | TradeSide.BUY | TradeType.MARKET | USD/BTC | 1.09 USD | 7849.99 | None
Before: Balance: 0.00 USD | Locked: 4972.43 USD | Balance: 0.00046373 BTC | Locked: 0.40947799 BTC
After: Balance: 0.00 USD | Locked: 4973.02 USD | Balance: 0.00046373 BTC | Locked: 0.40940239 BTC
Before: Balance: 0.59 USD | Locked: 4972.43 USD | Balance: 0.00046373 BTC | Locked: 0.40940239 BTC
After: Balance: 

Balance Wallet: Balance: 2.23 USD | Locked: 4968.60 USD
Order:  OrderStatus.PENDING | TradeSide.BUY | TradeType.MARKET | USD/BTC | 0.22 USD | 7746.63 | None
Before: Balance: 2.01 USD | Locked: 4968.82 USD | Balance: 0.00069643 BTC | Locked: 0.40943992 BTC
After: Balance: 2.01 USD | Locked: 4968.60 USD | Balance: 0.00069643 BTC | Locked: 0.40946815 BTC
Current price: 7746.63
Portfolio:          BTC  BTC_locked   USD  USD_locked    net_worth  step
0  0.000644     0.40944  3.28     4967.96  8137.122068  9099
0  0.000696     0.40944  2.87     4967.96  8137.488657  9100
0  0.000696     0.40944  2.55     4968.28  8148.976576  9101
0  0.000696     0.40944  2.23     4968.60  8131.312004  9102
0  0.000725     0.40944  2.01     4968.60  8148.003240  9103
Reward:  -0.004244045386254494
Current price: 7742.5
Profit loss:  0.814630926065
Current price: 7742.5
Action: TradeSide.SELL | USD/BTC | 0.25 | Stop Loss: 0.02
Balance Wallet: Balance: 0.00072466 BTC | Locked: 0.40943992 BTC
Order:  OrderStatu

Current price: 7671.77
Portfolio:          BTC  BTC_locked   USD  USD_locked    net_worth  step
0  0.000066    0.409637  5.06     4969.10  8124.361907  9112
0  0.000049    0.409637  5.19     4969.10  8132.354146  9113
0  0.000000    0.409686  5.19     4969.10  8132.968674  9114
0  0.000000    0.409686  5.19     4969.10  8146.271177  9115
0  0.000000    0.409686  4.45     4969.84  8117.306381  9116
Reward:  -0.004309750419977919
Current price: 7645.9
Profit loss:  0.8106707805104999
Current price: 7645.9
Action: TradeSide.SELL | USD/BTC | 0.14285714285714285 | None
Balance Wallet: Balance: 0.00000000 BTC | Locked: 0.40968595 BTC
Order:  None
Current price: 7645.9
Portfolio:          BTC  BTC_locked   USD  USD_locked    net_worth  step
0  0.000049    0.409637  5.19     4969.10  8132.354146  9113
0  0.000000    0.409686  5.19     4969.10  8132.968674  9114
0  0.000000    0.409686  5.19     4969.10  8146.271177  9115
0  0.000000    0.409686  4.45     4969.84  8117.306381  9116
0  0.000000 